In [6]:
import json
from pathlib import Path
from operator import itemgetter
import pandas as pd
import numpy as np
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score

import sys
import os

import plotly.graph_objs as go
import plotly.subplots as sp
from plotly.offline import init_notebook_mode, plot, iplot
import plotly.express as px
from plotly.subplots import make_subplots
 
module_path = os.path.abspath(os.path.join("../"))
if module_path not in sys.path:
    sys.path.append(module_path)

from data import *
from train import create_model
from evaluate import *

In [21]:
experiment = "App_test"
best = 100

In [22]:
# List all model directories
ray_results = Path("../../ray_results/")
model_dirs = [d for d in ray_results.iterdir() if d.is_dir()]

In [23]:
count_models(model_dirs, experiment)

Model_Type  Count
0                          FCN     20
1                         LSTM     20
2        LSTMTemporalAttention     20
3  LSTMSpatioTemporalAttention     20

In [24]:
model_dfs = {}
parameters = []
for model_dir in model_dirs:
    if experiment not in str(model_dir):
        continue
    rows = []
    best_checkpoints = find_best_checkpoints(model_dir, num_best=best)
    for i, (checkpoint, val_loss, params) in enumerate(best_checkpoints):
        
        # Load model and weights
        model = create_model(params)
        model = load_model_from_checkpoint(model, checkpoint)

        data_loader, scalers = get_dataloader(params)
        test_loader = data_loader['test']
        test_loader_length = len(test_loader.dataset)
        print("Number of values in test_loader:", test_loader_length)
        datetime_test = test_loader.datetime_index
        time_series_region = (datetime_test[0], datetime_test[-1])
        print("Time series region:", time_series_region)
        break
    break

Number of values in test_loader: 3295
Time series region: ('2020-05-08 02:00:00', '2020-09-22 08:00:00')


# Plotting the loss

In [25]:
for model_dir in model_dirs:
    if experiment not in str(model_dir):
        continue
    best_checkpoints = find_best_checkpoints(model_dir, num_best=1)
    for i, (checkpoint, val_loss, params) in enumerate(best_checkpoints):
        # Access run_dir from checkpoint_path
        print(f"Best model from {model_dir}")
        run_dir = checkpoint.parents[1]
        losses = get_losses(run_dir)
        plot_losses(losses)

Best model from ..\..\ray_results\App_test


# Hour ahead forecast

In [26]:
model_dfs , parameters = calculate_model_metrics(model_dirs, experiment, best)

In [27]:
# Create the data frame
df = pd.DataFrame(parameters)
df.sort_values("val_mea").head(20)

model_name   val_mea target_variable  sequence_length  \
0   LSTMSpatioTemporalAttention  0.000069  Flow_Kalltveit               25   
1         LSTMTemporalAttention  0.000103  Flow_Kalltveit               25   
2         LSTMTemporalAttention  0.000144  Flow_Kalltveit               25   
3   LSTMSpatioTemporalAttention  0.000176  Flow_Kalltveit               25   
4                          LSTM  0.000185  Flow_Kalltveit               25   
5   LSTMSpatioTemporalAttention  0.000194  Flow_Kalltveit               25   
6         LSTMTemporalAttention  0.000197  Flow_Kalltveit               25   
7         LSTMTemporalAttention  0.000329  Flow_Kalltveit               25   
8         LSTMTemporalAttention  0.000354  Flow_Kalltveit               25   
9                          LSTM  0.000371  Flow_Kalltveit               25   
10        LSTMTemporalAttention  0.000448  Flow_Kalltveit               25   
11        LSTMTemporalAttention  0.000473  Flow_Kalltveit               25   
12        LSTMTemporalAttention  0.000497  Flow_Kalltveit               25   
13                         LSTM  0.000546  Flow_Kalltveit               25   
14                         LSTM  0.000557  Flow_Kalltveit               25   
15                         LSTM  0.000563  Flow_Kalltveit               25   
16                         LSTM  0.000573  Flow_Kalltveit               25   
17                         LSTM  0.000671  Flow_Kalltveit               25   
18  LSTMSpatioTemporalAttention  0.000675  Flow_Kalltveit               25   
19        LSTMTemporalAttention  0.000688  Flow_Kalltveit               25   

    batch_size                            variables  train_size  val_size  \
0          512                       meteorological         0.7       0.2   
1          256        meteorological + hydrological         0.7       0.2   
2          256  meteorological + hydrological + hbv         0.7       0.2   
3          256                         hydrological         0.7       0.2   
4          256        meteorological + hydrological         0.7       0.2   
5          512                         hydrological         0.7       0.2   
6          256                         hydrological         0.7       0.2   
7          512  meteorological + hydrological + hbv         0.7       0.2   
8          512                         hydrological         0.7       0.2   
9          256                         hydrological         0.7       0.2   
10         256        meteorological + hydrological         0.7       0.2   
11         512        meteorological + hydrological         0.7       0.2   
12         256                         hydrological         0.7       0.2   
13         256  meteorological + hydrological + hbv         0.7       0.2   
14         256        meteorological + hydrological         0.7       0.2   
15         512                         hydrological         0.7       0.2   
16         512        meteorological + hydrological         0.7       0.2   
17         512                         hydrological         0.7       0.2   
18         512        meteorological + hydrological         0.7       0.2   
19         256  meteorological + hydrological + hbv         0.7       0.2   

    test_size  input_size  hidden_size  num_layers  output_size  \
0         0.1           7           32           4            1   
1         0.1          27           64           2            1   
2         0.1          36           64           4            1   
3         0.1          20           32           3            1   
4         0.1          27           64           3            1   
5         0.1          20           64           2            1   
6         0.1          20           32           3            1   
7         0.1          36           64           3            1   
8         0.1          20           64           3            1   
9         0.1          20           32           2            1   
10        0.1          27  

In [31]:
torch.cuda.empty_cache()

In [32]:
# concatenate the dataframes
df_concat_avg = pd.concat([model_dfs[k] for k in model_dfs.keys() if experiment in k])

df_concat_avg = df_concat_avg.drop(columns=['variables'])

# calculate the mean of each evaluation metric
df_avg = df_concat_avg.groupby(['model']).mean()
df_avg.sort_values("test_mae")

val_mae  test_mae       rmse        mape  \
model                                                                    
LSTMTemporalAttention        0.002504  3.041735   5.647437   35.107251   
LSTM                         0.002545  3.075442   5.607527   36.911819   
LSTMSpatioTemporalAttention  0.003470  3.636567   6.559969   42.035664   
FCN                          0.004615  6.747167  10.438297  108.759992   

                                   r2  testing (s)  
model                                               
LSTMTemporalAttention        0.350906     0.208941  
LSTM                         0.374780     0.137726  
LSTMSpatioTemporalAttention  0.162603     0.232437  
FCN                         -2.454864     0.061568

In [33]:
# concatenate the dataframes
df_concat_avg_w_var = pd.concat([model_dfs[k] for k in model_dfs.keys() if experiment in k])

# calculate the mean of each evaluation metric
df_avg_w_var = df_concat_avg_w_var.groupby(['model', 'variables']).mean()
model_var_counts = df_concat_avg_w_var.groupby(['model', 'variables']).size().reset_index(name='counts')
df_avg_w_var = df_avg_w_var.reset_index()  # reset index so that 'model' and 'variables' become regular columns
df_avg_w_var = pd.merge(df_avg_w_var, model_var_counts, on=['model', 'variables'])

df_avg_w_var.sort_values("test_mae")


model                            variables  \
4                          LSTM                         hydrological   
6                          LSTM        meteorological + hydrological   
14        LSTMTemporalAttention        meteorological + hydrological   
15        LSTMTemporalAttention  meteorological + hydrological + hbv   
12        LSTMTemporalAttention                         hydrological   
8   LSTMSpatioTemporalAttention                         hydrological   
9   LSTMSpatioTemporalAttention                       meteorological   
7                          LSTM  meteorological + hydrological + hbv   
10  LSTMSpatioTemporalAttention        meteorological + hydrological   
13        LSTMTemporalAttention                       meteorological   
5                          LSTM                       meteorological   
1                           FCN                       meteorological   
11  LSTMSpatioTemporalAttention  meteorological + hydrological + hbv   
0                           FCN                         hydrological   
3                           FCN  meteorological + hydrological + hbv   
2                           FCN        meteorological + hydrological   

     val_mae   test_mae       rmse        mape        r2  testing (s)  counts  
4   0.001062   1.713312   3.316790   20.027534  0.807211     0.101404       5  
6   0.002064   2.618064   5.076019   29.497132  0.456485     0.174091       5  
14  0.001894   2.620447   4.770831   30.220889  0.478907     0.194700       5  
15  0.002088   2.779485   5.369717   32.278442  0.427649     0.211945       5  
12  0.002083   2.844774   5.313459   33.055926  0.429007     0.198001       5  
8   0.002198   2.962536   5.123563   36.351012  0.442875     0.261048       5  
9   0.003121   3.140337   5.679652   36.085445  0.287137     0.195799       5  
7   0.002849   3.853391   6.662008   50.767874  0.196233     0.142848       5  
10  0.003901   3.919179   7.160097   45.271973  0.068003     0.247729       5  
13  0.003951   3.922234   7.135741   44.873748  0.068062     0.231119       5  
5   0.004204   4.117000   7.375289   47.354735  0.039190     0.132562       5  
1   0.003963   4.216690   7.833857   44.246339 -0.028323     0.044983       5  
11  0.004660   4.524214   8.276565   50.434226 -0.147605     0.225174       5  
0   0.004694   4.526997   8.168131   54.379853 -0.117784     0.064369       5  
3   0.005127   5.051422   8.557831   68.789698 -0.242893     0.068906       5  
2   0.004675  13.193563  17.193371  267.624078 -9.430454     0.068013       5

In [34]:
descriptive_statistics(df_concat_avg_w_var)


                            val_mae                                          \
                              count      mean       std       min       25%   
model                                                                         
FCN                            20.0  0.004615  0.000599  0.003842  0.004299   
LSTM                           20.0  0.002545  0.001930  0.000185  0.000570   
LSTMSpatioTemporalAttention    20.0  0.003470  0.001938  0.000069  0.001377   
LSTMTemporalAttention          20.0  0.002504  0.002153  0.000103  0.000424   

                                                          test_mae            \
                                  50%       75%       max    count      mean   
model                                                                          
FCN                          0.004672  0.004778  0.006687     20.0  6.747167   
LSTM                         0.001962  0.004605  0.004879     20.0  3.075442   
LSTMSpatioTemporalAttention  0.004651  0.00474

In [ ]:
box_plot(df_concat_avg_w_var)


In [ ]:
median_iqr(df_concat_avg_w_var)


Medians:
                               val_mae  test_mae      rmse       mape  \
model                                                                  
FCN                          0.004269  4.341619  7.875000  48.107953   
LSTM                         0.000423  1.665072  2.723103  22.777577   
LSTMSpatioTemporalAttention  0.000741  1.797732  3.093492  22.215264   
LSTMTemporalAttention        0.000235  1.313673  2.183057  17.445129   

                                   r2  testing (s)  
model                                               
FCN                         -0.039567     0.070253  
LSTM                         0.875763     0.110329  
LSTMSpatioTemporalAttention  0.839648     0.215710  
LSTMTemporalAttention        0.920165     0.118526  

IQR:
                               val_mae  test_mae      rmse       mape  \
model                                                                  
FCN                          0.001569  0.641404  1.698417  12.117548   
LSTM            

In [ ]:
# Calculate the confidence interval for each model and each metric
confidence_intervals = df_concat_avg_w_var.groupby('model').apply(lambda group: group[['val_mae', 'test_mae', 'rmse', 'mape', 'r2']].apply(confidence_interval))

print("Confidence Intervals:\n", confidence_intervals)

Confidence Intervals:
                                 val_mae  test_mae      rmse       mape  \
model                                                                    
FCN                         0  0.003227  3.661364  6.545788  43.105371   
                            1  0.003871  4.026332  7.250709  47.069679   
LSTM                        0  0.000697  1.972207  3.192961  27.127836   
                            1  0.001130  2.482522  3.896052  36.615785   
LSTMSpatioTemporalAttention 0  0.001319  2.066802  3.519981  25.844242   
                            1  0.002057  2.627747  4.566300  32.184744   
LSTMTemporalAttention       0  0.000333  1.387186  2.271948  18.739988   
                            1  0.000729  1.869340  3.035874  24.958747   

                                     r2  
model                                    
FCN                         0  0.079471  
                            1  0.221579  
LSTM                        0  0.685156  
                          

# Time-space consumption

In [ ]:
import pandas as pd
import json
from operator import itemgetter

def find_best_checkpoints_with_time(model_dir, num_best=5):
    checkpoints = []

    # Iterate over all training runs in the model directory
    for run_dir in model_dir.iterdir():
        if run_dir.is_dir():
            # Read the progress.csv file to get the validation losses and training time
            progress_file = run_dir / "progress.csv"
            if progress_file.exists():
                with open(run_dir / "params.json", "r") as f:
                    params = json.load(f)
                progress_data = pd.read_csv(progress_file)

                best_val_idx = progress_data["val_loss"].idxmin()
                best_val_loss = progress_data.loc[best_val_idx, "val_loss"]
                training_time = progress_data.loc[best_val_idx, "time_total_s"]

                # Save the checkpoint path, validation loss, and training time
                checkpoint_path = run_dir / "my_model" / "checkpoint.pt"
                checkpoints.append((checkpoint_path, best_val_loss, training_time, params))

    # Sort the checkpoints based on validation loss
    checkpoints.sort(key=itemgetter(1))

    return checkpoints[:num_best]

In [ ]:
import torch
import numpy as np
import pandas as pd

results = {}

for model_dir in model_dirs:
    if experiment not in str(model_dir):
        continue

    best_checkpoints = find_best_checkpoints_with_time(model_dir, num_best=best)

    for i, (checkpoint, val_loss, training_time, params) in enumerate(best_checkpoints):
        # Load model and weights
        model = create_model(params)
        
        # Calculate space consumption
        num_parameters = sum(p.numel() for p in model.parameters())
        space_consumption = num_parameters * 4  # 4 bytes per parameter (float32)
        
        model_name = params['model']
        if model_name not in results:
            results[model_name] = {'val_loss': [], 'training_time': [], 'testing_time': [], 'space_consumption': []}

        results[model_name]['val_loss'].append(val_loss)
        results[model_name]['training_time'].append(training_time)
        results[model_name]['space_consumption'].append(space_consumption)

        # Add testing time to results
        testing_time = np.mean(model_dfs[model_dir.name]['testing (s)'])
        results[model_name]['testing_time'].append(testing_time)

df = pd.DataFrame(columns=['Model', 'Avg val_loss', 'Avg training_time', 'Avg testing_time', 'Avg space_consumption'])

for model_name, data in results.items():
    avg_val_loss = np.mean(data['val_loss'])
    avg_training_time = np.mean(data['training_time'])
    avg_testing_time = np.mean(data['testing_time'])
    avg_space_consumption = np.mean(data['space_consumption']) / 1024 # Space consumption in KB

    df = pd.concat([df, pd.DataFrame({
        'Model': [model_name],
        'Avg val_loss': [avg_val_loss],
        'Avg training_time': [avg_training_time],
        'Avg testing_time': [avg_testing_time],
        'Avg space_consumption': [avg_space_consumption] # Space consumption in KB
    })])

df.sort_values("Avg training_time")


Model  Avg val_loss  Avg training_time  \
0                          FCN      0.003549          48.380466   
0                         LSTM      0.000914          72.635314   
0        LSTMTemporalAttention      0.000531          80.207395   
0  LSTMSpatioTemporalAttention      0.001688         160.597930   

   Avg testing_time  Avg space_consumption  
0          0.067597              32.665156  
0          0.134787             180.011328  
0          0.134219             150.583672  
0          0.227791             221.015938

# Attention weights understanding 

In [54]:
from plotly.subplots import make_subplots

def visualize_attention(attention_weights_spatial, attention_weights_temporal, batch_idx, features):
    # Extract attention weights for a specific batch element
    attention_matrix_spatial = attention_weights_spatial[batch_idx].detach().cpu().numpy()
    attention_matrix_temporal = attention_weights_temporal[batch_idx].detach().cpu().numpy()

    # Create a subplot with 1 row and 2 columns
    fig = make_subplots(rows=1, cols=2, subplot_titles=("Spatial Attention Weights", "Temporal Attention Weights"))

    # Add spatial attention heatmap to subplot
    fig.add_trace(
        go.Heatmap(
            z=attention_matrix_spatial,
            x=[f'f{i}' for i in range(1, attention_matrix_spatial.shape[1] + 1)],
            y=[f't-{i}' for i in range(1, attention_matrix_spatial.shape[0] + 1)],
            colorscale='Viridis',
            name="Spatial Weights"
        ), 
        row=1, col=1
    )

    # Add temporal attention heatmap to subplot
    fig.add_trace(
        go.Heatmap(
            z=attention_matrix_temporal,
            y=[f't-{i}' for i in range(1, attention_matrix_temporal.shape[0] + 1)],
            x=[f'f{i}' for i in range(1, attention_matrix_temporal.shape[1] + 1)],
            colorscale='Viridis',
            name="Temporal Weights"
        ), 
        row=1, col=2
    )

    fig.update_layout(
        width=1800,
        height=800,
        xaxis_title="Features",
        yaxis_title="Input Time Step",
    )
    fig.show()


def plot_attention(params, spatial_weights=None, temporal_weights=None):
    features = [params["data"]['target_variable']] + params["data"]["variables"]
    b = 20
    # If the attention weights are torch tensors, convert them to numpy arrays first
    if isinstance(spatial_weights, torch.Tensor) and isinstance(temporal_weights, torch.Tensor):
        visualize_attention(spatial_weights, temporal_weights, batch_idx=b, features=features)


In [55]:
for model_dir in model_dirs:
    if experiment not in str(model_dir):
        continue
    print(f"Best performing model on experiment: {os.path.basename(model_dir)}")
    rows = []
    best_checkpoints = find_best_checkpoints(model_dir, num_best=1)
    for i, (checkpoint, val_loss, params) in enumerate(best_checkpoints):
        if params['model'] == "LSTM" or params['model'] == "FCN":
            continue
        elif params['model'] == "LSTMTemporalAttention":
            continue

        # Load model and weights
        model = create_model(params)
        model = load_model_from_checkpoint(model, checkpoint)
        data_loader, _ = get_dataloader(params)
        test_dataloader = data_loader["test"]

        # Get a batch of input sequences and their corresponding targets
        inputs, targets = next(iter(test_dataloader))

        output, spatial_attention_weights, temporal_attention_weights = model(inputs, True)
        
        plot_attention(params, spatial_attention_weights, temporal_attention_weights)

Best performing model on experiment: data_4-PBT-fcn
Best performing model on experiment: data_4-PBT-lstm
Best performing model on experiment: data_4-PBT-spa_temp


Best performing model on experiment: data_4-PBT-temp
Best performing model on experiment: data_4-PBT2-fcn
Best performing model on experiment: data_4-PBT2-lstm
Best performing model on experiment: data_4-PBT2-spa_temp


Best performing model on experiment: data_4-PBT2-temp
Best performing model on experiment: data_4-PBT3-fcn
Best performing model on experiment: data_4-PBT3-lstm
Best performing model on experiment: data_4-PBT3-spa_temp


KeyboardInterrupt: 

In [ ]:
# Create a dictionary to store the top models
top_models = {}
n_models = 1
# Iterate over all the directories containing the models
for model_dir in model_dirs:
    # Skip directories not related to the current experiment
    if experiment not in str(model_dir):
        continue

    # Find the best checkpoints for each model
    best_checkpoints = find_best_checkpoints(model_dir, num_best=best)

    for i, (checkpoint, val_loss, params) in enumerate(best_checkpoints):
        # Load the model and its weights
        model = create_model(params)
        model = load_model_from_checkpoint(model, checkpoint)

        # Calculate performance metrics
        data_loader, scalers = get_dataloader(params)
        test_loader = data_loader['test']
        with torch.no_grad():
            y_preds, y_test = get_preds_actuals(model, test_loader)
        
        y_preds = d.inverse_transform_target(np.array(y_preds).reshape(-1, 1), scalers['Flow_Kalltveit'])
        y_test = d.inverse_transform_target(np.array(y_test).reshape(-1, 1), scalers['Flow_Kalltveit'])
            
        mae = mean_absolute_error(y_test, y_preds)
        rmse = np.sqrt(mean_squared_error(y_test, y_preds))
        mape = mean_absolute_percentage_error(y_test, y_preds)
        r2 = r2_score(y_test, y_preds)

        # Save the model and its parameters if it's among the top four
        if len(top_models) < n_models or mae < max(top_models.keys()):
            if len(top_models) == n_models:
                # Remove the model with the highest MAE
                del top_models[max(top_models.keys())]
            # Save the model and its parameters
            top_models[mae] = {
                "model": model,
                "params": params,
                "metrics": {
                    "val_mae": val_loss,
                    "test_mae": mae,
                    "rmse": rmse,
                    "mape": mape,
                    "r2": r2,
                }
            }

KeyboardInterrupt: 

# Multi-time step ahead forecasting

In [21]:
steps_ahead = 12

In [31]:
def recursive_forecast(model, input, forecast_steps=1, return_weights=False):
    predictions = []
    attention_weights = []

    # Find the index of the target feature in the input_size dimension
    target_feature_idx = 0

    for i in range(forecast_steps):
        if return_weights:
            out, alpha_list, beta_t = model(input, return_weights=True)
            if i+1 in {1, 4, 8, 12}:
                attention_weights.append((alpha_list, beta_t))
        else:
            out = model(input)

        predictions.append(out)

        input[:, -1, target_feature_idx] = out.squeeze(-1)

    predictions = torch.stack(predictions, dim=1)

    if return_weights:
        return predictions, attention_weights
    else:
        return predictions

def get_multi_step_preds_actuals(model, test_loader, forecast_steps=3, return_weights=False):
    y_preds = []
    y_test = []
    attention_weights_all = []

    device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

    # Move the model to the GPU
    model.to(device)

    for input, target in test_loader:
        # Calculate the number of elements that can be reshaped
        num_elements_to_reshape = target.shape[0] // forecast_steps * forecast_steps

        # Slice the input tensor to match the reshaped target tensor
        input_sliced = input[::forecast_steps][:num_elements_to_reshape // forecast_steps]

        input_sliced = input_sliced.to(device)
        if return_weights:
            predictions, attention_weights = recursive_forecast(model, input_sliced, forecast_steps, return_weights=True)
            attention_weights_all.append(attention_weights)
        else:
            predictions = recursive_forecast(model, input_sliced, forecast_steps)

        y_preds.append(predictions)

        # Slice the target tensor to keep only the elements that can be reshaped
        target_sliced = target[:num_elements_to_reshape]

        # Reshape the sliced target tensor to match the forecast_steps
        reshaped_target = target_sliced.view(-1, forecast_steps)
        y_test.append(reshaped_target)

    y_preds = torch.cat(y_preds).detach().cpu().numpy()
    y_test = torch.cat(y_test).detach().cpu().numpy()

    if return_weights:
        return y_preds, y_test, attention_weights_all
    else:
        return y_preds, y_test

In [ ]:
def plot_pred_actual(data_loader, scalers, model, model_name, forecast_steps=3):
    val_loader, test_loader = data_loader['val'], data_loader['test']

    y_val = [j for _, j in val_loader]
    y_val = torch.cat(y_val).detach().cpu().numpy()
    
    with torch.no_grad():
        y_preds, y_test = get_multi_step_preds_actuals(model, test_loader, forecast_steps)

    y_val = d.inverse_transform_target(np.array(y_val).reshape(-1, 1), scalers['Flow_Kalltveit'])
    y_preds = d.inverse_transform_target(np.array(y_preds).reshape(-1, 1), scalers['Flow_Kalltveit'])
    y_test = d.inverse_transform_target(np.array(y_test).reshape(-1, 1), scalers['Flow_Kalltveit'])

    # Get datetime values
    datetime_val = val_loader.datetime_index
    datetime_test = test_loader.datetime_index

    # Slice the datetime values to match the reshaped target values
    datetime_test_sliced = datetime_test[:len(y_preds)]

    # Create dataframes
    val_df = pd.DataFrame({'datetime': datetime_val, 'target': y_val.flatten()})
    test_df = pd.DataFrame({'datetime': datetime_test_sliced, 'target': y_test.flatten()})
    predictions_df = pd.DataFrame({'datetime': datetime_test_sliced, 'predictions': y_preds.flatten()})

    # Create a scatter plot for each dataset
    fig = go.Figure()

    fig.add_trace(go.Scatter(x=val_df['datetime'], y=val_df['target'],
                        mode='lines', name='Validation'))
    fig.add_trace(go.Scatter(x=test_df['datetime'], y=test_df['target'],
                        mode='lines', name='Test'))
    fig.add_trace(go.Scatter(x=predictions_df['datetime'], y=predictions_df['predictions'],
                        mode='lines', name='Predictions'))

    # Add spread plot between Test and Predictions
    fig.add_trace(go.Scatter(x=test_df['datetime'], y=test_df['target'], fill=None,
                             mode='lines', line_color='rgba(0, 0, 0, 0.1)', showlegend=False))
    fig.add_trace(go.Scatter(x=predictions_df['datetime'], y=predictions_df['predictions'], fill='tonexty',
                             mode='lines', line_color='rgba(0, 0, 0, 0.1)', name='Spread'))

    # Add axis labels and plot title
    fig.update_layout(
        title=f'Time Series Data with {model_name} Predictions',
        xaxis_title='Datetime',
        yaxis_title='Target Value',
    )

    # Show the plot
    fig.show()
    
model_dfs = {}
for model_dir in model_dirs:
    if experiment not in str(model_dir):
        continue
    rows = []
    best_checkpoints = find_best_checkpoints(model_dir, num_best=1)
    for i, (checkpoint, val_loss, params) in enumerate(best_checkpoints):
        # Load model and weights
        model = create_model(params)
        model = load_model_from_checkpoint(model, checkpoint)

        data_loader, scalers = get_dataloader(params)
        test_loader = data_loader['test']
        
        plot_pred_actual(data_loader, scalers, model, params['model'], forecast_steps=steps_ahead)


In [32]:
def plot_pred_actual(fig, data_loader, scalers, model, model_name, forecast_steps=3):
    test_loader = data_loader['test']

    with torch.no_grad():
        y_preds, y_test = get_multi_step_preds_actuals(model, test_loader, forecast_steps)

    y_preds = d.inverse_transform_target(np.array(y_preds).reshape(-1, 1), scalers['Flow_Kalltveit'])

    datetime_test = test_loader.datetime_index
    datetime_test_sliced = datetime_test[:len(y_preds)]

    predictions_df = pd.DataFrame({'datetime': datetime_test_sliced, 'predictions': y_preds.flatten()})

    fig.add_trace(go.Scatter(x=predictions_df['datetime'], y=predictions_df['predictions'],
                        mode='lines', name=f'Predictions - {model_name}'))
    return fig


model_dfs = {}
fig = go.Figure()  # create a common figure for all models

for model_dir in model_dirs:
    if experiment not in str(model_dir):
        continue

    best_checkpoints = find_best_checkpoints(model_dir, num_best=1)
    for checkpoint, val_loss, params in best_checkpoints:
        model = create_model(params)
        model = load_model_from_checkpoint(model, checkpoint)

        data_loader, scalers = get_dataloader(params)
        test_loader = data_loader['test']

        if model_dir == model_dirs[0]:
            val_loader = data_loader['val']
            y_val = [j for _, j in val_loader]
            y_val = torch.cat(y_val).detach().cpu().numpy()
            y_val = d.inverse_transform_target(np.array(y_val).reshape(-1, 1), scalers['Flow_Kalltveit'])
            datetime_val = val_loader.datetime_index
            val_df = pd.DataFrame({'datetime': datetime_val, 'target': y_val.flatten()})
            fig.add_trace(go.Scatter(x=val_df['datetime'], y=val_df['target'],
                            mode='lines', name='Validation'))
            
            y_test = [j for _, j in test_loader]
            y_test = torch.cat(y_test).detach().cpu().numpy()
            y_test = d.inverse_transform_target(np.array(y_test).reshape(-1, 1), scalers['Flow_Kalltveit'])
            datetime_test = test_loader.datetime_index
            test_df = pd.DataFrame({'datetime': datetime_test, 'target': y_test.flatten()})
            fig.add_trace(go.Scatter(x=test_df['datetime'], y=test_df['target'],
                                mode='lines', name='Test'))

        fig = plot_pred_actual(fig, data_loader, scalers, model, params['model'], forecast_steps=steps_ahead)

fig.update_layout(
    title=f'Time Series Data with Multiple Models Predictions',
    xaxis_title='Datetime',
    yaxis_title='Target Value',
)
fig.show()


IndexError: index 16 is out of bounds for dimension 2 with size 16

In [ ]:
torch.cuda.empty_cache()

In [ ]:
model_dfs = {}
for model_dir in model_dirs:
    if experiment not in str(model_dir):
        continue
    
    rows = []
    best_checkpoints = find_best_checkpoints(model_dir, num_best=best)
    for i, (checkpoint, val_loss, params) in enumerate(best_checkpoints):
        
        # Load model and weights
        model = create_model(params)
        model = load_model_from_checkpoint(model, checkpoint)

        data_loader, scalers = get_dataloader(params)
        test_loader = data_loader['test']
        
        with torch.no_grad():
            y_preds, y_test = get_multi_step_preds_actuals(model, test_loader, forecast_steps=steps_ahead)

        y_preds = d.inverse_transform_target(np.array(y_preds).reshape(-1, 1), scalers['Flow_Kalltveit'])
        y_test = d.inverse_transform_target(np.array(y_test).reshape(-1, 1), scalers['Flow_Kalltveit'])

        
        # Calculate the Mean Absolute Error (MAE)
        mae = mean_absolute_error(y_test, y_preds)
        # Calculate the Root Mean Squared Error (RMSE)
        rmse = np.sqrt(mean_squared_error(y_test, y_preds))
        # Calculate the Mean Absolute Percentage Error (MAPE)
        mape = mean_absolute_percentage_error(y_test, y_preds)
        # Calculate the Determination Coefficient (R^2)
        r2 = r2_score(y_test, y_preds)

        model_variables = params["data"]["variables"]
        variables_category = categorize_features(model_variables)

        rows.append(
            {
                "model": params["model"],
                "val_mae": val_loss,
                "test_mae": mae,
                "rmse": rmse,
                "mape": mape,
                "r2": r2,
                "variables": variables_category,
            }
        )
    df = pd.DataFrame(rows)
    model_dfs[model_dir.name] = df

In [ ]:
model_dfs.get(f"data_4-{experiment}-lstm").sort_values("test_mae")

model   val_mae  test_mae      rmse        mape        r2  \
8   LSTM  0.000143  2.122022  4.010515   25.295725  0.733952   
20  LSTM  0.000215  2.237649  4.151003   28.269964  0.714987   
2   LSTM  0.000111  2.249005  4.575430   23.169816  0.653724   
18  LSTM  0.000212  2.256394  4.168571   27.531317  0.712569   
24  LSTM  0.000228  2.276967  4.078093   29.545155  0.724911   
..   ...       ...       ...       ...         ...       ...   
77  LSTM  0.001583  5.840369  8.129394   78.713846 -0.093139   
74  LSTM  0.001517  5.948903  8.020076  118.730748 -0.063938   
71  LSTM  0.000782  5.953946  7.856533   82.098562 -0.020989   
89  LSTM  0.002537  6.038497  8.174090   90.022999 -0.105193   
75  LSTM  0.001571  6.286995  8.455630   87.383312 -0.182636   

                              variables  
8                        meteorological  
20                       meteorological  
2                        meteorological  
18                       meteorological  
24                       meteorological  
..                                  ...  
77  meteorological + hydrological + hbv  
74  meteorological + hydrological + hbv  
71  meteorological + hydrological + hbv  
89  meteorological + hydrological + hbv  
75  meteorological + hydrological + hbv  

[100 rows x 7 columns]

In [ ]:
model_dfs.get(f"data_4-{experiment}-temp").sort_values("test_mae")

model   val_mae  test_mae       rmse        mape  \
14  LSTMTemporalAttention  0.000098  2.155408   3.974777   27.908185   
5   LSTMTemporalAttention  0.000088  2.167864   3.972512   25.888529   
7   LSTMTemporalAttention  0.000090  2.187603   3.991739   25.907630   
4   LSTMTemporalAttention  0.000088  2.191984   3.975775   28.117585   
0   LSTMTemporalAttention  0.000064  2.208612   4.070525   25.764000   
..                    ...       ...       ...        ...         ...   
70  LSTMTemporalAttention  0.000315  7.509598   9.625455  105.144715   
69  LSTMTemporalAttention  0.000313  7.710547   9.841772  108.142757   
76  LSTMTemporalAttention  0.000359  7.750612   9.936705  107.884943   
81  LSTMTemporalAttention  0.000492  7.766866   9.983623  108.105230   
65  LSTMTemporalAttention  0.000271  9.277541  12.111920  124.817467   

          r2                      variables  
14  0.738673                 meteorological  
5   0.738970                 meteorological  
7   0.736438                 meteorological  
4   0.738542                 meteorological  
0   0.725931                 meteorological  
..       ...                            ...  
70 -0.532504  meteorological + hydrological  
69 -0.602160  meteorological + hydrological  
76 -0.633217  meteorological + hydrological  
81 -0.648676  meteorological + hydrological  
65 -1.426527                   hydrological  

[100 rows x 7 columns]

In [ ]:
model_dfs.get(f"data_4-{experiment}-spa_temp").sort_values("test_mae")

model   val_mae  test_mae      rmse       mape  \
13  LSTMSpatioTemporalAttention  0.000122  2.166414  4.134457  25.057402   
7   LSTMSpatioTemporalAttention  0.000119  2.174302  4.199373  24.262853   
10  LSTMSpatioTemporalAttention  0.000121  2.175518  4.077469  25.429723   
15  LSTMSpatioTemporalAttention  0.000124  2.205461  4.092118  25.587866   
6   LSTMSpatioTemporalAttention  0.000118  2.222720  4.131452  25.192100   
..                          ...       ...       ...       ...        ...   
42  LSTMSpatioTemporalAttention  0.000721  6.305377  8.732101  79.286957   
56  LSTMSpatioTemporalAttention  0.000768  6.397627  8.831419  81.049031   
47  LSTMSpatioTemporalAttention  0.000735  6.523944  8.892444  83.944923   
21  LSTMSpatioTemporalAttention  0.000233  6.914121  9.229859  93.099111   
51  LSTMSpatioTemporalAttention  0.000744  6.947420  9.256016  91.464025   

          r2                      variables  
13  0.717254                 meteorological  
7   0.708306                 meteorological  
10  0.724995                 meteorological  
15  0.723016                 meteorological  
6   0.717665                 meteorological  
..       ...                            ...  
42 -0.261237  meteorological + hydrological  
56 -0.290091  meteorological + hydrological  
47 -0.307981  meteorological + hydrological  
21 -0.409124                   hydrological  
51 -0.417122  meteorological + hydrological  

[100 rows x 7 columns]

In [ ]:
# concatenate the dataframes
df_concat_avg = pd.concat([model_dfs[k] for k in model_dfs.keys() if experiment in k])

df_concat_avg = df_concat_avg.drop(columns=['variables'])

# calculate the mean of each evaluation metric
df_avg = df_concat_avg.groupby(['model']).mean()
df_avg.sort_values("test_mae")

val_mae  test_mae      rmse       mape        r2
model                                                                         
LSTM                         0.000914  4.008736  6.451920  48.194605  0.288437
LSTMTemporalAttention        0.000531  4.291006  6.689504  52.538056  0.205429
LSTMSpatioTemporalAttention  0.001688  4.406033  7.140974  52.832035  0.113387
FCN                          0.003549  6.617174  9.577326  95.378434 -0.593250

In [ ]:
# concatenate the dataframes
df_concat_avg_w_var = pd.concat([model_dfs[k] for k in model_dfs.keys() if experiment in k])

# calculate the mean of each evaluation metric
df_avg_w_var = df_concat_avg_w_var.groupby(['model', 'variables']).mean()
model_var_counts = df_concat_avg_w_var.groupby(['model', 'variables']).size().reset_index(name='counts')
df_avg_w_var = df_avg_w_var.reset_index()  # reset index so that 'model' and 'variables' become regular columns
df_avg_w_var = pd.merge(df_avg_w_var, model_var_counts, on=['model', 'variables'])

df_avg_w_var.sort_values("test_mae")


model                            variables  \
13        LSTMTemporalAttention                       meteorological   
9   LSTMSpatioTemporalAttention                       meteorological   
5                          LSTM                       meteorological   
6                          LSTM        meteorological + hydrological   
15        LSTMTemporalAttention  meteorological + hydrological + hbv   
4                          LSTM                         hydrological   
12        LSTMTemporalAttention                         hydrological   
11  LSTMSpatioTemporalAttention  meteorological + hydrological + hbv   
8   LSTMSpatioTemporalAttention                         hydrological   
7                          LSTM  meteorological + hydrological + hbv   
1                           FCN                       meteorological   
2                           FCN        meteorological + hydrological   
10  LSTMSpatioTemporalAttention        meteorological + hydrological   
14        LSTMTemporalAttention        meteorological + hydrological   
0                           FCN                         hydrological   
3                           FCN  meteorological + hydrological + hbv   

     val_mae  test_mae       rmse        mape        r2  counts  
13  0.000146  2.500608   4.357568   30.880483  0.682144      25  
9   0.001057  2.793112   5.057264   32.419516  0.533133      25  
5   0.000849  3.173299   5.491072   37.880113  0.458988      25  
6   0.000711  3.931560   6.182529   47.985626  0.361197      25  
15  0.000415  4.079786   6.480012   48.909134  0.303228      25  
4   0.000843  4.111189   6.898307   45.116660  0.205954      25  
12  0.000588  4.171729   6.921359   47.045703  0.183320      25  
11  0.002694  4.339721   7.255809   53.265068  0.117341      25  
8   0.001201  4.780661   7.713861   56.185964  0.009778      25  
7   0.001251  4.818896   7.235770   61.796021  0.127610      25  
1   0.004011  4.874056   8.081980   61.365115 -0.081187      25  
2   0.004663  5.141120   8.676233   66.306511 -0.291128      25  
10  0.001800  5.710637   8.536961   69.457592 -0.206704      25  
14  0.000974  6.411901   8.999076   83.316902 -0.346976      25  
0   0.004717  6.750108  10.132796   88.456551 -0.817199      25  
3   0.000805  9.703411  11.418296  165.385558 -1.183487      25

In [ ]:
# concatenate the dataframes
descriptive_statistics(df_concat_avg_w_var)

                            val_mae                                          \
                              count      mean       std       min       25%   
model                                                                         
FCN                           100.0  0.003549  0.001621  0.000754  0.003116   
LSTM                          100.0  0.000914  0.001090  0.000102  0.000229   
LSTMSpatioTemporalAttention   100.0  0.001688  0.001858  0.000109  0.000298   
LSTMTemporalAttention         100.0  0.000531  0.000996  0.000064  0.000121   

                                                          test_mae            \
                                  50%       75%       max    count      mean   
model                                                                          
FCN                          0.004269  0.004685  0.004972    100.0  6.617174   
LSTM                         0.000423  0.001530  0.004963    100.0  4.008736   
LSTMSpatioTemporalAttention  0.000741  0.00438

In [ ]:
box_plot(df_concat_avg_w_var)

In [ ]:
median_iqr(df_concat_avg_w_var)

Medians:
                               val_mae  test_mae      rmse       mape        r2
model                                                                         
FCN                          0.004269  4.801335  8.281553  60.156149 -0.134443
LSTM                         0.000423  4.104466  6.622497  46.867178  0.274558
LSTMSpatioTemporalAttention  0.000741  4.533261  7.624690  52.175838  0.038379
LSTMTemporalAttention        0.000235  3.991304  6.502899  45.915572  0.300522

IQR:
                               val_mae  test_mae      rmse        mape  \
model                                                                   
FCN                          0.001569  4.489285  2.438297  102.793820   
LSTM                         0.001301  1.008911  1.342047   17.149689   
LSTMSpatioTemporalAttention  0.004086  0.889403  1.916488   10.764273   
LSTMTemporalAttention        0.000220  1.238110  2.184163   16.734451   

                                   r2  
model                         

In [ ]:
# Calculate the confidence interval for each model and each metric
confidence_intervals = df_concat_avg_w_var.groupby('model').apply(lambda group: group[['val_mae', 'test_mae', 'rmse', 'mape', 'r2']].apply(confidence_interval))

print("Confidence Intervals:\n", confidence_intervals)

Confidence Intervals:
                                 val_mae  test_mae       rmse        mape  \
model                                                                      
FCN                         0  0.003227  6.063864   9.149771   84.347534   
                            1  0.003871  7.170483  10.004883  106.409334   
LSTM                        0  0.000697  3.814932   6.216712   45.029399   
                            1  0.001130  4.202540   6.687128   51.359811   
LSTMSpatioTemporalAttention 0  0.001319  4.154304   6.818937   49.527715   
                            1  0.002057  4.657761   7.463010   56.136355   
LSTMTemporalAttention       0  0.000333  3.966795   6.327934   47.825193   
                            1  0.000729  4.615217   7.051072   57.250918   

                                     r2  
model                                    
FCN                         0 -0.749002  
                            1 -0.437499  
LSTM                        0  0.239850  
      